### The file aims for the demonstration of the methdology pipeline, please used our new designed database (new excel attached )

#### The following code is when user put a new news article link into the model, the model will extract the headline , Date and Content

In [14]:
import requests
from bs4 import BeautifulSoup
from datetime import datetime


def get_article_details(article_url):
    response = requests.get(article_url)
    soup = BeautifulSoup(response.content, "html.parser")

    # Extract headline
    headline_tag = soup.find("h1")
    headline = (
        headline_tag.get_text(strip=True) if headline_tag else "No headline found"
    )

    # Attempt to extract publication date with error handling
    date_container = soup.find("div", class_="article-publish")
    if date_container:
        # Extract the text and handle cleaning it up
        date_text = date_container.get_text(strip=True)
        # Extract the first date assuming it's the publication date (before "Updated:")
        publication_date_text = date_text.split("(Updated:")[0].strip()
        try:
            publication_date = datetime.strptime(
                publication_date_text, "%d %b %Y %I:%M%p"
            ).strftime("%Y-%m-%d %H:%M:%S")
        except ValueError:
            publication_date = "No publication date found"
    else:
        publication_date = "No publication date found"

    # Extract main content of the article
    article_body = soup.find("article")
    if not article_body:
        article_body = soup
    article_text = (
        article_body.get_text(separator=" ", strip=True)
        if article_body
        else "No article content found"
    )

    return headline, publication_date, article_text


# Example usage
article_url = "https://www.channelnewsasia.com/singapore/singapore-airlines-stops-using-iran-airspace-israel-hamas-war-middle-east-escalation-4264011"
headline, publication_date, article_content = get_article_details(article_url)
print("Headline:", headline)
print("Publication Date:", publication_date)
print("Content:", article_content[:500])  # Print the first 500 characters to check

Headline: Singapore Airlines stops using Iranian airspace as 'precautionary measure' amid Middle East tensions
Publication Date: 2024-04-14 08:58:00
Content: Advertisement Singapore Singapore Airlines stops using Iranian airspace as 'precautionary measure' amid Middle East tensions Singapore Airlines says it is closely monitoring the situation in the Middle East. (File photo: REUTERS/Edgar Su) New: You can now listen to articles. Sorry, the audio is unavailable right now. Please try again later. This audio is AI-generated. 14 Apr 2024 08:58AM (Updated: 14 Apr 2024 06:15PM) Bookmark Bookmark Share WhatsApp Telegram Facebook Twitter Email LinkedIn SING


#### Here is the code for Summarization of the aritlce (PLEASE USE UR OWN OPENAI KEY HAHA)

In [9]:
import openai


openai.api_key = ""


def summarize_article(article_content):
    try:
        # Generating the prompt for GPT-3
        prompt_text = (
            "Summarize the following article in about 70 words, focusing on "
            "what happened, where it happened, and the consequences (economic loss, environmental impact, etc.):\n\n"
            f"{article_content}"
        )

        # Call to OpenAI's Completion API
        response = openai.Completion.create(
            engine="gpt-3.5-turbo-instruct",
            prompt=prompt_text,
            temperature=0.5,
            max_tokens=60,  # Adjust as needed to fit the summary length
            top_p=1,
            frequency_penalty=0,
            presence_penalty=0,
        )

        # Extracting the text from the response
        summary = response.choices[0].text.strip()
        return summary
    except Exception as e:
        print(f"An error occurred: {e}")
        return ""


summary = summarize_article(article_content)
print("Summary:", summary)

Summary: Singapore Airlines has stopped using Iranian airspace as a precautionary measure amid tensions in the Middle East. This decision was made after Iran launched more than 200 drones and missiles at Israel, causing concerns for the safety of flights. The move by Singapore Airlines mirrored that of other airlines, including Lufth


In [10]:
unique_categories = df["Category"].unique()
print(unique_categories)

['Mine Workers Strike' 'Travel Warning' 'Port Congestion'
 'Bombing, Police Operations'
 'Roadway Closure / Disruption, Flooding, Severe Winds, Weather Advisory'
 'Cargo/Warehouse Theft' 'Tropical Cyclone / Storm' 'Storm' 'Earthquake'
 'Workplace Accident' 'Tornado' 'Industrial Action'
 'Public Safety / Security' 'Public Transportation Disruption'
 'General Strike' 'Protest / Riot' 'Port Disruption, Severe Winds'
 'Miscellaneous Events' 'Customs Regulation' 'Port Disruption'
 'Port Disruption, Weather Advisory' 'Port Disruption,Port Congestion'
 'Flooding' 'Train Delays / Disruption,Cargo Disruption'
 'Port Disruption, Customs Delay' 'Security Advisory' 'Weather Advisory'
 'Port Closure' 'Customs Delay'
 'Public Safety / Security, Weather Advisory' 'Trade Regulation'
 'Trade Restrictions' 'Organized Crime'
 'Roadway Closure / Disruption, Public Safety / Security'
 'Military Operations, Ground Transportation Advisory'
 'Ground Transportation Advisory'
 'Protest / Riot, Ground Transporta

In [11]:
import openai


def classify_article(article_content):
    prompt = f"""Read the following article and classify its content into one of these categories: 'Aviation Advisory',
'Bombing',
'Cargo Disruption',
'Warehouse Theft',
'Chemical Spill',
'Injury',
'Earthquake',
'Flooding',
'Ground Transportation Advisory',
'Hazmat Response',
'Ice Storm',
'Individuals in Focus',
'Industrial Action',
'Maritime Accident',
'Maritime Accident.Ground Transportation Advisory',
'Maritime Advisory',
'Mine Workers Strike',
'Miscellaneous Events',
'Miscellaneous Strikes',
'Network Disruption',
'Non-industrial Fire',
'Police Operations',
'Port Closure',
'Port Congestion',
'Port Disruption',
'Power Outage',
'Production Halt',
'Protest',
'Public Safety ,
'Public Transportation Disruption',
'Roadway Closuren',
'Severe Winds',
'Storm',
'Tornado',
'Train Delays,
'Travel Warning',
'Tropical Cyclone Storm',
'Typhoon',
'Vehicle Accident',
'Weather Advisory',
'Workplace Accident'
Summary: {article_content}
Category:"""

    response = openai.Completion.create(
        engine="gpt-3.5-turbo-instruct",  # Adjust according to the latest available and appropriate model
        prompt=prompt,
        temperature=0.7,
        max_tokens=60,  # Adjust based on your needs
        top_p=1.0,
        frequency_penalty=0,
        presence_penalty=0,
        stop=["\n"],  # Stop generating further when a newline character is encountered
    )
    category = response.choices[0].text.strip()
    return category

In [12]:
import requests
from bs4 import BeautifulSoup


def fetch_article_content(url):
    response = requests.get(url)
    soup = BeautifulSoup(response.content, "html.parser")
    article_text = " ".join([p.text for p in soup.find_all("p")])
    return article_text

In [15]:
import openai


def classify_article(url):
    # Fetch article content
    article_content = fetch_article_content(url)

    # Construct the classification prompt
    prompt = f"""Read the following article and classify its content into one of these categories:
    'Aviation Advisory', 'Bombing',
'Cargo Disruption',
'Chemical Spill',
'Death',
'Earthquake',
'Flooding',
'Ground Transportation Advisory',
'Hazmat Response',
'Ice Storm',
'Individuals in Focus',
'Industrial Action',
'Maritime Accident',
'Maritime Accident.Ground Transportation Advisory',
'Maritime Advisory',
'Mine Workers Strike',
'Miscellaneous Events',
'Miscellaneous Strikes',
'Network Disruption',
'Non-industrial Fire',
'Police Operations',
'Port Closure',
'Port Congestion',
'Port Disruption',
'Power Outage',
'Production Halt',
'Protest / Riot',
'Public Safety / Security',
'Public Transportation Disruption',
'Roadway Closure / Disruption',
'Severe Winds',
'Storm',
'Tornado',
'Train Delays / Disruption',
'Travel Warning',
'Tropical Cyclone / Storm',
'Typhoon',
'Vehicle Accident',
'Weather Advisory',
'Workplace Accident', ...
    
    Article:
    {article_content}
    
    Category:"""

    # Classify using OpenAI GPT-3
    response = openai.Completion.create(
        engine="gpt-3.5-turbo-instruct",  # Ensure using a correct and non-deprecated model
        prompt=prompt,
        temperature=0.7,
        max_tokens=60,
        top_p=1.0,
        frequency_penalty=0,
        presence_penalty=0,
        stop=["\n"],  # Stop generating further when a newline character is encountered
    )
    category = response.choices[0].text.strip()
    return category


# Example usage
url = "https://www.channelnewsasia.com/singapore/singapore-airlines-stops-using-iran-airspace-israel-hamas-war-middle-east-escalation-4264011"
category = classify_article(url)
print("Category:", category)

Category: Aviation Advisory


#### Now you the classfication result, which is quite accurate :))

In [15]:
print(headline)

2 dead, 3 missing in Guangzhou after cargo ship rams bridge over Pearl River


#### Update our database!

In [23]:
import pandas as pd
from datetime import datetime


def update_database(file_path, url):
    # Fetch details from the article
    headline, publication_date, article_content = get_article_details(article_url)
    summary = summarize_article(article_content)
    category = classify_article(url)

    new_data = {
        "Headline": headline,
        "Summary": summary,
        "Category": category,
        "Datetime": publication_date,
        "URL": article_url,
    }

    # Load the existing data from the CSV file
    try:
        df = pd.read_csv(file_path)
    except FileNotFoundError:
        # If the file does not exist, create a new DataFrame
        df = pd.DataFrame(
            columns=["id", "Headline", "Summary", "Category", "Datetime", "URL"]
        )
        new_id = 1  # Start with ID 1 if no file exists
    else:
        # If IDs exist, increment from the last used ID
        new_id = df["id"].max() + 1 if not df.empty else 1

    # Prepare the new data entry
    new_entry = pd.DataFrame(
        {
            "id": [new_id],
            "Headline": [new_data["Headline"]],
            "Summary": [new_data["Summary"]],
            "Category": [new_data["Category"]],
            "Datetime": [new_data["Datetime"]],
            "URL": [new_data["URL"]],
        }
    )

    # Append the new data entry to the DataFrame using concat
    df = pd.concat([df, new_entry], ignore_index=True)

    # Save the updated DataFrame back to CSV
    df.to_csv(file_path, index=False)
    print(f"Database updated successfully with ID {new_id}.")


# Example usage
url = "https://www.channelnewsasia.com/singapore/singapore-airlines-stops-using-iran-airspace-israel-hamas-war-middle-east-escalation-4264011"
file_path = "cleaned_data1.csv"
update_database(file_path, url)

Database updated successfully with ID 16.


In [30]:
import pandas as pd


def rank_related_articles(file_path, category):
    # Load the existing data from the CSV file
    try:
        df = pd.read_csv(file_path)
    except FileNotFoundError:
        print("Database file not found.")
        return

    # Filter articles by the specified category
    filtered_df = df[df["Category"] == category]

    # Convert 'Datetime' from string to datetime objects for accurate sorting
    filtered_df["Datetime"] = pd.to_datetime(filtered_df["Datetime"])

    # Sort articles by 'Datetime' in descending order to get the most recent articles first
    sorted_df = filtered_df.sort_values(by="Datetime", ascending=False)

    # Display the sorted DataFrame
    print(sorted_df[["id", "Headline", "Summary", "Category", "Datetime", "URL"]])
    return sorted_df


# Example usage
file_path = "cleaned_data1.csv"
category = "Aviation Advisory"
ranked_articles = rank_related_articles(file_path, category)

    id                                           Headline  \
22  28  UPDATE 1 - Attacks on tanker and oil facility ...   
24  30  WATCH FOR: Road, rail, air, and maritime cargo...   
21  27  The Search and Rescue Agencies of  Indonesia a...   
20  22  Hurricane Isaias to Impact Florida Coast this ...   
23  29  UPDATE 1 - Australia unlikely to directly reta...   
19  21  Beirut International Airport suffers damage fr...   
18  20  Air Arabia flight G9-661 bound for Khartoum ma...   
17  19  Victoria Harbour - Reports of a plane crash we...   
16  18  UPDATE: Pakistan partially closes 3 internatio...   
14  15  Gatwick Airport (LGW) - British Airways flight...   
15  17  UPDATE - USA: Hurricane Dorian forecast to imp...   
13  14  Delta Flight 472 met by PAPD firefighters at J...   

                                              Summary           Category  \
22  An explosion caused damage to the Greek-operat...  Aviation Advisory   
24  Risk analysis: Several trade unions including ... 

/var/folders/65/44v_jv_n0qx33txj6vvbf1k00000gn/T/ipykernel_31218/1610732821.py:15: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  filtered_df['Datetime'] = pd.to_datetime(filtered_df['Datetime'])
/var/folders/65/44v_jv_n0qx33txj6vvbf1k00000gn/T/ipykernel_31218/1610732821.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['Datetime'] = pd.to_datetime(filtered_df['Datetime'])


In [33]:
import pandas as pd
from tabulate import tabulate


def print_ranked_articles_tabulate(file_path, category):
    try:
        df = pd.read_csv(file_path)
        df["Datetime"] = pd.to_datetime(df["Datetime"])
        filtered_df = df[df["Category"] == category]
        sorted_df = filtered_df.sort_values(by="Datetime", ascending=False)

        # Print DataFrame using tabulate
        print(tabulate(sorted_df, headers="keys", tablefmt="pretty", showindex=False))
    except FileNotFoundError:
        print("Database file not found.")


# Example usage
file_path = "cleaned_data1.csv"
category = "Aviation Advisory"
print_ranked_articles_tabulate(file_path, category)

+----+-------------------------------------------------------------------------------------------------------------------------------------------------------------+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

/var/folders/65/44v_jv_n0qx33txj6vvbf1k00000gn/T/ipykernel_31218/2109249609.py:7: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df['Datetime'] = pd.to_datetime(df['Datetime'])
